<a href="https://colab.research.google.com/github/MengOonLee/WebScrapy/blob/master/Groceries/Lotus.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%bash
pip install --no-cache-dir -qU scrapy selenium

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 290.1/290.1 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 53.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 476.0/476.0 kB 256.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 238.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 254.1/254.1 kB 210.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.6/97.6 kB 138.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.6/74.6 kB 229.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 124.4 MB/s eta 0:00:00


In [2]:
%%writefile Lotus.py
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
import scrapy
from scrapy.crawler import CrawlerProcess

class LotusSpider(scrapy.Spider):
    name = 'Lotus'

    def __init__(self, **kwargs):
        super().__init__(**kwargs)
        options = webdriver.chrome.options.Options()
        options.add_argument("--headless")
        options.add_argument("--no-sandbox")
        options.add_argument("--enable-javascript")
        options.add_argument("--enable-cookies")
        options.add_argument("--disable-notifications")
        options.add_argument("--disable-web-security")
        options.add_argument("--incognito")
        self.driver = webdriver.Chrome(options=options)

    def start_requests(self):
        urls = [
            "https://www.lotuss.com.my/en/category/meat-poultry/meat/parts-weighted"
        ]
        for url in urls:
            yield scrapy.Request(url=url, callback=self.parse_categories)

    def parse_categories(self, response):
        self.driver.get(response.url)

        elem_present = ""
        while not elem_present:
            try:
                elem_present = self.driver.find_element(By.XPATH,
                    "//div[@class='product-grid-item']"
                )
            except:
                continue

        selector = scrapy.Selector(text=self.driver.page_source)
        category = selector.css("h1#category-title::text").get()
        print(category)
        category_links = selector.css("div.carousel a")
        if len(category_links)!=0:
            yield from response.follow_all(category_links,
                callback=self.parse_categories)
        else:
            last_height = self.driver.execute_script(
                "return document.body.scrollHeight"
            )

            while True:
                self.driver.execute_script(
                    "window.scrollTo(0, document.body.scrollHeight)"
                )
                time.sleep(3)
                new_height = self.driver.execute_script(
                    "return document.body.scrollHeight"
                )
                if new_height==last_height:
                    break
                last_height = new_height

            selector = scrapy.Selector(text=self.driver.page_source)
            item_links = selector.css("div#product-list a")

            yield from response.follow_all(item_links,
                callback=self.parse_items)

    def parse_items(self, response):
        self.driver.get(response.url)

        elem_present = ""
        while not elem_present:
            try:
                elem_present = self.driver.find_element(By.XPATH, """
                    //img[@id='current-product-image']
                """)
            except:
                continue

        selector = scrapy.Selector(text=self.driver.page_source)
        item = selector.css("div.MuiBox-root")
        name = item.css("h1::text").get()
        price = item.css("::text")[3:6].getall()
        price = "".join(price)
        print(name, price)

process = CrawlerProcess()
process.crawl(LotusSpider)
process.start()

Writing Lotus.py


In [3]:
%%bash
python Lotus.py

Parts & Weighted
None ©Lotuss Stores (Malaysia) Sdn Bhd (Registration No. 200001018812 (521419-K)) 2024V - 2.2.1
CHICKEN WHOLE LEG KG (7191) RM15.85/Kg
LOTUS'S FRESH SLICE BEEF 300G RM16.99/Each
LOTUS'S FRESH AUS LAMB SHOULDER SLICE (5319) RM28.97/Kg
LOTUSS AUSTRALIA BEEF BRISKET SHABU-SHABU 180G RM14.49/Each
BUFFALO MINCE KG (5818) RM19.89/Kg
None ©Lotuss Stores (Malaysia) Sdn Bhd (Registration No. 200001018812 (521419-K)) 2024V - 2.2.1
INDIA BUFFALO BLOCK KG (5574) RM21.87/Kg
AUSTRALIA MUTTON CUBES (5317) RM26.87/Kg
GOURMESSA BEEF BREAKFAST STREAKY 100G RM11.59/Each
WHOLE CHICKEN WITH HEAD AND FEET (7730) RM6.99/Kg
CHICKEN WING KG (7190) RM15.60/Kg
CHICKEN RIB KG (6226) RM9.88/Kg
CHICKEN DRUMSTICK KG (7192) RM15.50/Kg
CHICKEN THIGH KG (6229) RM10.76/Kg


2024-08-17 08:49:06 [scrapy.utils.log] INFO: Scrapy 2.11.2 started (bot: scrapybot)
2024-08-17 08:49:06 [scrapy.utils.log] INFO: Versions: lxml 4.9.4.0, libxml2 2.10.3, cssselect 1.2.0, parsel 1.9.1, w3lib 2.2.1, Twisted 24.7.0, Python 3.10.12 (main, Jul 29 2024, 16:56:48) [GCC 11.4.0], pyOpenSSL 24.2.1 (OpenSSL 3.2.2 4 Jun 2024), cryptography 42.0.8, Platform Linux-6.1.85+-x86_64-with-glibc2.35
2024-08-17 08:49:06 [selenium.webdriver.common.selenium_manager] DEBUG: Selenium Manager binary found at: /usr/local/lib/python3.10/dist-packages/selenium/webdriver/common/linux/selenium-manager
2024-08-17 08:49:06 [selenium.webdriver.common.selenium_manager] DEBUG: Executing process: /usr/local/lib/python3.10/dist-packages/selenium/webdriver/common/linux/selenium-manager --browser chrome --language-binding python --output json
2024-08-17 08:49:17 [selenium.webdriver.common.selenium_manager] DEBUG: Driver path: /root/.cache/selenium/chromedriver/linux64/127.0.6533.119/chromedriver
2024-08-17 08